<a href="https://colab.research.google.com/github/ajasja/RosettaCrashCourse/blob/main/02_Interactive_make_bundles.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
#@title Setup and import packages
#@markdown A free license is needed for Rosetta and PyRosetta and can be obtained at: https://els2.comotion.uw.edu/product/rosetta and https://els2.comotion.uw.edu/product/pyrosetta 
#@markdown PyRosetta will be installed into your google drive (which is why the notebook asks for access to it).

#@markdown Created by Ajasja Ljubetič (https://twitter.com/AjasjaLjubetic).
# Notebook setup
import sys
if 'google.colab' in sys.modules:
    !pip install pyrosettacolabsetup
    import pyrosettacolabsetup
    pyrosettacolabsetup.install_pyrosetta()

  #base notebook https://nbviewer.org/github/RosettaCommons/PyRosetta.notebooks/blob/master/notebooks/06.06-Introduction-to-Parametric-backbone-design.ipynb
  #base notebook https://nbviewer.org/github/RosettaCommons/PyRosetta.notebooks/blob/master/notebooks/02.08-Visualization-and-pyrosetta.distributed.viewer.ipynb
import pyrosetta
pyrosetta.init("-auto_setup_metals 1 -detect_disulf 1 -beta_cart -mute all")  

!pip install py3Dmol
import pyrosetta.distributed.viewer as viewer
from pyrosetta.rosetta.protocols.helical_bundle import *
from pyrosetta.rosetta.core.select.residue_selector import ChainSelector
from pyrosetta.distributed import io
import py3Dmol
import math
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
from ipywidgets.widgets import IntSlider, FloatSlider, Checkbox, ToggleButtons, HBox, VBox, Button, Text

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Mounted at /content/google_drive
Looking for compatible PyRosetta wheel file at google-drive/PyRosetta/colab.bin/wheels...
Found compatible wheel: /content/google_drive/MyDrive/PyRosetta/colab.bin/wheels//content/google_drive/MyDrive/PyRosetta/colab.bin/wheels/pyrosetta-2022.20+release.1eb2c329089-cp37-cp37m-linux_x86_64.whl
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


PyRosetta-4 2022 [Rosetta PyRosetta4.MinSizeRel.python37.ubuntu 2022.20+release.1eb2c32908941b039e4f87163ff0cb442419288d 2022-05-21T10:32:36] retrieved from: http://www.pyrosetta.org
(C) Copyright Rosetta Commons Member Institutions. Created in JHU by Sergey Lyskov and PyRosetta Team.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


## Bundle parameters ([MakeBundleMover](https://www.rosettacommons.org/docs/latest/scripting_documentation/RosettaScripts/Movers/movers_pages/MakeBundleMover))
* **lenght**: lenght of the helix in residues.
* **r0**: Major helix radius, in Angstroms.
* **omega0**: Major helix twist per residue (in degrees).
* **delta_omega1**: Rotation of a helix about its own axis (in degrees).
* **invert**: run the helix in the other direction (up vs down).

In [2]:
#@title Run the bundle editor
p = py3Dmol.view()
p.setStyle({'cartoon': {'color':'chain'}});

pose = pyrosetta.rosetta.core.pose.Pose()
mb = MakeBundle() 

mb.set_reset_pose(True)
mb.set_use_degrees(True)
num_helices = 4

def update_bundle():     
  mb.apply(pose)
  p.removeAllModels()
  p.addModels(io.to_pdbstring(pose), "pdb")
  p.setStyle({'cartoon': {'color':'spectrum'}})
  p.update()

def initialize_bundle():
  for i in range(1, num_helices+1):
    mb.add_helix()
    mb.helix(i).set_helix_length(length.value)
    mb.helix(i).calculator_op().real_parameter(BPC_delta_omega0).set_value(360/num_helices*(i-1))
    mb.helix(i).calculator_op().real_parameter(BPC_r0).set_value(r0.value) #in angstrem

chosen_helix=ToggleButtons(options=['all', 1, 2, 3, 4], description='chosen_helix')
#delta_omega0=FloatSlider(min=-5, max=5, step=0.5, value=0,  description='delta_omega0') 
r0=FloatSlider(min=1, max=10, step=0.1, value=5, description='r0') 
length=IntSlider(min=14, max=50, value=28, description='length')
omega0=FloatSlider(min=-5, max=5, step=0.1, value=0, description='omega0')
delta_omega1=FloatSlider(min=0, max=360, description='delta_omega1',  style= {'description_width': 'initial'})
invert=Checkbox(value=False, description='invert')

def on_length_change(change):
  for i in range(1, num_helices+1):
    if chosen_helix.value=='all' or chosen_helix.value==i:
      mb.helix(i).set_helix_length(length.value)
  update_bundle()

def on_param_change(change):
  """Takes the name of the parameter from the change.owner.description and se"""
  for i in range(1, num_helices+1):
    if chosen_helix.value=='all' or chosen_helix.value==i:
      param_enum = getattr(pyrosetta.rosetta.protocols.helical_bundle, f'BPC_{change.owner.description}')
      mb.helix(i).calculator_op().real_parameter(param_enum).set_value(change.new)
  update_bundle()

def on_invert_change(change):
  for i in range(1, num_helices+1):
    if chosen_helix.value=='all' or chosen_helix.value==i:
      mb.helix(i).calculator_op().boolean_parameter(BPC_invert_helix).set_value(bool(change.new))
  update_bundle()

length.observe(on_length_change, names='value')
r0.observe(on_param_change, names='value')
omega0.observe(on_param_change, names='value')
delta_omega1.observe(on_param_change, names='value')
invert.observe(on_invert_change, names='value')

save_button = Button(description='save PDB')
save_edit = Text(value='bundle.pdb')
def save_pdb(sender):
  pose.dump_pdb(save_edit.value)
save_button.on_click(save_pdb)
save_box = HBox([save_button, save_edit])

display(chosen_helix, length, r0, omega0, delta_omega1, invert, save_box, p)
initialize_bundle()
update_bundle()

ToggleButtons(description='chosen_helix', options=('all', 1, 2, 3, 4), value='all')

IntSlider(value=28, description='length', max=50, min=14)

FloatSlider(value=5.0, description='r0', max=10.0, min=1.0)

FloatSlider(value=0.0, description='omega0', max=5.0, min=-5.0)

FloatSlider(value=0.0, description='delta_omega1', max=360.0, style=SliderStyle(description_width='initial'))

Checkbox(value=False, description='invert')

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol